# EPS 109 FINAL

In [1]:
%matplotlib osx 

import numpy as np
import scipy.integrate
import glob
import re
import astropy.constants as const
import astropy.units as u
import matplotlib.pyplot as plt
from matplotlib import animation
from mpl_toolkits.mplot3d import Axes3D
from matplotlib.animation import FFMpegWriter
import matplotlib.image as mpimg
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
from __future__ import print_function
import ipywidgets as widgets
from IPython.display import display
from IPython.display import HTML
from ipywidgets import interact, interactive, fixed, interact_manual
from ipywidgets import GridspecLayout

In [2]:
class AstroObject:
    def __init__(self, mass, init_position, init_velocity, radius):
        self.mass = mass
        self.init_position = init_position
        self.init_velocity = init_velocity
        self.radius = radius

    def set_mass(self, mass):
        self.mass = mass

    def set_distance(self, init_position):
        self.init_position = init_position

def gravity(rv, t, star_mass, planet_mass):
    r1 = rv[:2] 
    v1 = rv[2:4] 
    r12 = np.linalg.norm(r1)
    
    dv1bydt = planet_mass * (-r1)/(pow(r12, 3))
    dr1bydt = v1
    
    derivatives = np.concatenate((dr1bydt, dv1bydt))
    return derivatives

class Planet(AstroObject):
    def __init__(self, mass, init_position, init_velocity, color, image, implemented=True):
        mass_planet = mass * 10**(-5)
        super().__init__(mass_planet, init_position, init_velocity, ((mass_planet/7.36*np.pi)**(1./3.)))
        self.implemented = implemented
        self.color = color
        self.image = image

    def __str__(self):
        return f'Planet: Mass={self.mass}, Radius={self.radius}, Distance={self.init_position[0]}, Velocity={self.init_velocity[1]}'

    def set_implemented(self, status):
        self.implemented = status

class Star(AstroObject):
    def __init__(self, mass, radius, init_position=[0,0], init_velocity=[0, 0]):
        super().__init__(mass, init_position, init_velocity, radius)

    def __str__(self):
        return f'Star {self.name}. Mass={self.mass}, Radius={self.radius}'

class SolarSystem:
    def __init__(self, star, planets=[]):
        self.star = star
        self.planets = planets

    def get_planet_masses(self):
        masses = []
        for planet in self.planets:
            if planet.implemented:
                masses.append(planet.mass)
        return masses

    def get_planet_distances(self):
        distances = []
        for planet in self.planets:
            if planet.implemented:
                distances.append(planet.init_position[0])
        return distances

    def most_massive_planet(self):
        masses = self.get_planet_masses()
        largest = max(masses)
        for planet in self.planets:
            if planet.implemented and planet.mass == largest:
                return planet
        return None

    def farthest_planet(self):
        distances = self.get_planet_distances()
        farthest = max(distances)
        for planet in self.planets:
            if planet.implemented and planet.init_position[0] == farthest:
                return planet
        return None

#solar system with static values
p1 = Planet(0.5, [120, 0], [0, 0.1], color='yellow', image='IMG_1126.PNG', implemented=True) #90 is good too 
p2 = Planet(0.5, [90, 0], [0, 0.1], color='aquamarine', image='IMG_1129.PNG', implemented=True) #50 is a good think to stay
sun = Star(mass=1, radius=109.0) #maybe make the image here? 
test_system = SolarSystem(sun, [p1, p2])

# Initialize writer 
metadata = dict(title='Orbit', artist='Matplotlib')
writer = FFMpegWriter(fps=5, metadata=metadata, bitrate=200000)  #frame rates
fig = plt.figure(dpi=200)

# Set up and solving the ODE for motion of each planet
time_span = np.linspace(0, max(test_system.get_planet_distances()) * 300, 120)
axes_limits_x = [-max(test_system.get_planet_distances()) * 10, max(test_system.get_planet_distances()) * 10]
axes_limits_y = [-max(test_system.get_planet_distances()) * 10, max(test_system.get_planet_distances()) * 5]

all_orbit_solutions = []

for planet in test_system.planets:
    if planet.implemented:
        init_params = np.array([planet.init_position, planet.init_velocity])
        init_params = init_params.flatten()

        sol = scipy.integrate.odeint(gravity, init_params, time_span, args=(planet.mass, test_system.star.mass))
        sol_for_planet = sol[:, :2]
        all_orbit_solutions.append(sol_for_planet)

largest_r = max(test_system.planets[i].radius for i in range(len(test_system.planets)))
largest_depth = largest_r / test_system.star.radius
depth_transit = 1 - (largest_depth * 10)

all_videos = glob.glob("videos_generated\*")
all_digits = []

for vid in all_videos:
    matched = re.findall(r'\d+', vid)
    if matched:
        digits = int(matched[0])
        all_digits.append(digits)

print(all_digits)

if all_digits:
    next_idx = max(all_digits) + 1
else:
    next_idx = 1

fig, ax = plt.subplots(figsize=(12, 8))
bg_img = mpimg.imread("space2.jpeg")

def getImage(path):
    return OffsetImage(plt.imread(path, format="PNG"), zoom=0.025)

paths = [planet.image for planet in test_system.planets]

with writer.saving(fig, "my_solar_system_" + str(next_idx) + ".mp4", dpi=200):
    for i in range(len(time_span)):
        ax.clear()
        interpolation_points = 10000
        for planet_idx in range(len(test_system.planets)):
            if test_system.planets[planet_idx].implemented:
                planet_sols = all_orbit_solutions[planet_idx]

                planet_img = mpimg.imread(test_system.planets[planet_idx].image)
                
                interp_indices = np.linspace(0, len(planet_sols) - 1, interpolation_points, dtype=int)
                interp_orbit = planet_sols[interp_indices]
                
                ax.plot(planet_sols[:i, 0], planet_sols[:i, 1], color=test_system.planets[planet_idx].color, alpha=0.5, linewidth=2.0)

                ab = AnnotationBbox(getImage(paths[planet_idx]), (planet_sols[i, 0], planet_sols[i, 1]), frameon=False)
                ax.add_artist(ab)

        ax.imshow(bg_img, extent=[-200, 200, -200, 200])
        ax.scatter(0, 0, color="orange", marker="*", s=3000, zorder=5) #sun

        ax.set_xlim(-200, 200)
        ax.set_ylim(-200, 200)

        plt.draw()
        plt.pause(0.01)
        writer.grab_frame()


[44, 50, 51, 45, 53, 47, 46, 52, 42, 43, 41, 55, 54, 40, 27, 33, 4, 5, 32, 26, 30, 24, 18, 7, 6, 19, 25, 31, 35, 21, 2, 3, 20, 34, 22, 36, 1, 37, 23, 12, 13, 11, 39, 38, 10, 28, 14, 15, 29, 17, 8, 9, 16, 48, 49]
